# Visualizing Planet Tanager Data Interactively with HyperCoast

[![image](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/opengeos/HyperCoast/blob/main/docs/examples/tanager.ipynb)


This notebook demonstrates how to visualize the [Planet Tanager hyperspectral data](https://www.planet.com/data/stac/browser/tanager-core-imagery/catalog.json) interactively with HyperCoast.


Tanager-1 (launched August 2024) carries a high-precision Dyson imaging spectrometer onboard Planet’s next-generation smallsat bus. Tanager provides high spectral resolution (~5 nm) across the full 380–2500 nm VSWIR spectral range. For more details, please refer to the [Planet Tanager data release page](https://www.planet.com/pulse/unleash-the-power-of-hyperspectral-over-50-tanager-radiance-datasets-now-available-on-planet-s).

## Install packages

Uncomment the following line to install the packages.

In [1]:
%pip install hypercoast

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 119.6/119.6 kB 6.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 629.4/629.4 kB 25.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 70.5/70.5 kB 7.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 201.0/201.0 kB 12.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 175.5/175.5 kB 18.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.1/17.1 MB 97.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 882.2/882.2 kB 64.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.5/9.5 MB 115.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 6.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.0/86.0 kB 9.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 20.5/20.5 MB 116.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.8/2.8 MB 111.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 22.

## Import libraries

In [2]:
import hypercoast

## Find Tanager data

Browse the Tanager data on the [Planet STAC browser](https://www.planet.com/data/stac/browser/tanager-core-imagery/catalog.json?.language=en). Find the data you want to visualize.

For example, we want to visualize the data of the [coastal water bodies in the San Francisco Bay area](https://www.planet.com/data/stac/browser/tanager-core-imagery/coastal-water-bodies/20250514_193937_64_4001/20250514_193937_64_4001.json?.asset=asset-basic_radiance_hdf5).
Click on the "Copy URL" button to get the direct URL of the data.

![](https://github.com/user-attachments/assets/c0107919-c36a-4d92-9886-2701b282ff5c)

## Download Tanager data

Once you have the URL of the data, you can download the data using the following code:

In [3]:
url = "https://storage.googleapis.com/open-cogs/planet-stac/release1-basic-radiance/20250514_193937_64_4001_basic_radiance.h5"

In [4]:
file_path = hypercoast.download_file(url)

## Read Tanager data

We can read the Tanager data using the `read_tanager` function. It will return a `xarray.Dataset` object. The `toa_radiance` variable is the top of atmosphere radiance. It has 426 spectral bands. Note that the dataset is not gridded. We will need to interpolate the data to a regular grid for visualization on an interactive map.

In [5]:
dataset = hypercoast.read_tanager(file_path)
dataset

<xarray.Dataset> Size: 710MB
Dimensions:       (wavelength: 426, y: 680, x: 607)
Coordinates:
  * wavelength    (wavelength) float64 3kB 376.4 381.4 ... 2.494e+03 2.499e+03
    fwhm          (wavelength) float64 3kB 5.39 5.42 5.45 5.48 ... 5.21 5.2 5.2
    latitude      (y, x) float64 3MB 38.01 38.01 38.01 ... 37.78 37.78 37.78
    longitude     (y, x) float64 3MB -122.4 -122.4 -122.4 ... -122.2 -122.2
Dimensions without coordinates: y, x
Data variables:
    toa_radiance  (wavelength, y, x) float32 703MB 81.07 79.31 ... 0.1747 0.1923
Attributes:
    source:     Planet Tanager HDF5
    stac_item:  https://www.planet.com/data/stac/tanager-core-imagery/coastal...

![](https://github.com/user-attachments/assets/da1b044b-69fa-400f-a750-55872c2e2f5e)

## Visualize Tanager data

Let's visualize the Tanager data on an interactive map. Specify the bands to visualize. You can visualize the data in the spectral space or the RGB space.

In [6]:
m = hypercoast.Map()
m.add_tanager(dataset, bands=[100, 60, 50], vmin=0, vmax=120, layer_name="Tanager")
m

Map(center=[37.894428000000005, -122.302098], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom…

Alternatively, you can visualize a single band of the Tanager data and specify a colormap.

In [7]:
m = hypercoast.Map()
m.add_tanager(dataset, bands=[100], colormap="jet", layer_name="Tanager")
m

Map(center=[37.894428000000005, -122.302098], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom…

## Change band combinations interactively

To change the band combinations interactively, you can use spectral tool to select the bands you want to visualize.

In [8]:
m = hypercoast.Map()
m.add_tanager(dataset, bands=[100, 60, 50])
m.add("spectral")
m

Map(center=[37.894428000000005, -122.302098], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom…

## Visualize spectral signatures

To visualize the spectral signatures, you can use the `spectral` tool. Simply click on the map to visualize the spectral signatures.

In [9]:
m = hypercoast.Map()
m.add_tanager(dataset, bands=[100, 60, 50])
m.add("spectral")
m

Map(center=[37.894428000000005, -122.302098], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom…